In [1]:
import torch
import yaml
import os

# Humandoid MARL
from Humanoid_MARL.envs.base_env import GymWrapper, VectorGymWrapper
from Humanoid_MARL.utils.torch_utils import save_models, load_models
from Humanoid_MARL.agent.ppo.train_humanoids import Agent, eval_unroll, get_agent_actions
from Humanoid_MARL.envs.torch_wrapper import TorchWrapper
from IPython.display import HTML, clear_output
from brax.io import html
import jax
from Humanoid_MARL import envs
from Humanoid_MARL.utils.utils import load_reward_config, load_config

In [2]:
env_name = "ants"
config = load_config(env_name)
env = envs.create(config['env_name'], auto_reset=False, **config['env_config'])
env = GymWrapper(env, get_jax_state=True)
env = TorchWrapper(env, device=config['train_config']['device'], get_jax_state=True)

# model = "models/20240412_133034_ppo_ants_82575360.pt"
# model = "models/20240412_133034_ppo_ants_41287680.pt" # Good 1
# model = "models/20240412_133034_ppo_ants_82575360.pt" # Good 2
# model = "models/20240412_133034_ppo_ants_115015680.pt" # BAD 2
# model = "models/20240412_162055_ppo_ants_655360.pt"
# model = "20240422_173637_ppo_humanoids_1544110080.pt"  # Good
model = "20240506_143007_ppo_ants_283115520.pt"

model_path = os.path.join("../models/", model)
# env warmup
observation = env.reset()
action = torch.zeros(env.action_space.shape[0] * env.num_agents).to(config['train_config']['device'])
env.step(action)
agents = load_models(model_path, Agent, device=config['train_config']['device'])
jax_states = []
num_steps = 1000

eval_reward = 0.0
episodes = torch.zeros((), device = config['train_config']['device'])
for i in range(num_steps):
    print(f"{i} / {num_steps}")
    logits, action = get_agent_actions(agents, observation, env.obs_dims)
    if config['agent_config'].get("freeze_idx"):
        action[:,config['agent_config'].get("freeze_idx") * 8:(config['agent_config'].get("freeze_idx") * 8) + 8] = torch.ones_like(action[:,config['agent_config'].get("freeze_idx") * 8:(config['agent_config'].get("freeze_idx") * 8) + 8]) * 0
    jax_state, observation, reward, done, info = env.step(Agent.dist_postprocess(action[0]))
    episodes += torch.sum(done)
    jax_states.append(jax_state)
    print(f"{i} | {info} | DONE [{done}] | Reward [{reward}]")
    print(f"{i} | Action {action}")
    eval_reward += reward
    if done:
        observation = env.reset()
        print(f"Episode Done")
        print(f"Total Reward | {eval_reward / episodes}")
print(f"Total Reward | {eval_reward / episodes}")

Models loaded from ../models/20240506_143007_ppo_ants_283115520.pt
0 / 1000
0 | {'angle_penalty': tensor([-0.0027, -0.0025], device='cuda:0'), 'distance_from_origin': tensor([0.0937, 2.0577], device='cuda:0'), 'forward_reward': tensor([0., 0.], device='cuda:0'), 'reward_chase': tensor([-1.0212,  1.0212], device='cuda:0'), 'reward_ctrl': tensor([-0., -0.], device='cuda:0'), 'reward_forward': tensor([-0., 0.], device='cuda:0'), 'reward_survive': tensor([0., 0.], device='cuda:0'), 'reward_tag': tensor([0., -0.], device='cuda:0'), 'stand_up_reward': tensor([0., 0.], device='cuda:0'), 'steps': tensor(2., device='cuda:0'), 'truncation': tensor(0., device='cuda:0'), 'wall_penalty': tensor([-5.9257e-28, -1.3850e-19], device='cuda:0'), 'x_position': tensor([-0.0166,  2.0577], device='cuda:0'), 'x_velocity': tensor([-0.1998,  0.0116], device='cuda:0'), 'y_position': tensor([0.0922, 0.0187], device='cuda:0'), 'y_velocity': tensor([0.0021, 0.0210], device='cuda:0'), 'z_position': tensor([0.7457, 0

In [5]:
HTML(html.render(env.sys, [jax_state.pipeline_state for jax_state in jax_states])) 

In [6]:
HTML(html.render(env.sys, [jax_state.pipeline_state for jax_state in jax_states])) 